In [ ]:
import re
import jieba.posseg as pseg
import thulac
import json
import time

def get_couple(sent,entities,relations,relation_map):
    count = 0
    pattern = '(原告|被告)?<e(\d)>([^<>]*[其|我|要求])?[诉|与|同|和|、]?(原告|被告)?<e(\d)>[^。！；<>]*(结婚|夫妻|婚后|离婚|婚姻)' #夫妻
    res = re.search(pattern,sent)
    if res:
        a,b = int(res.group(2)),int(res.group(5))
        if a== b:
            return count
        rela = [entities[a-1],entities[b-1],'夫妻']
        print('couple relation:',' '.join(rela))
        if rela not in relations and [entities[b-1],entities[a-1],'夫妻'] not in relations:
            relations.append(rela)
        count += 1
    return count

def get_daili(sent,entities,relations,relation_map):
    count = 0
    pattern = '<e(\d)>.{,2}(特别授权)?(委托|法定)代理人<e(\d)>' #代理人
    res = re.search(pattern,sent)
    if res:
        a,b = int(res.group(1)),int(res.group(4))
        if a == b:
            return count
        rela = [entities[b-1],entities[a-1],'代理人']
        print('代理 relation:',' '.join(rela))
        if rela not in relations:
            relations.append(rela)
        count += 1
    return count
        
def get_xi(sent,entities,relations,relation_map): # a系bxx
    count = 0
    pattern = '<e(\d)>[（，]?[系是](原告|被告)?<e(\d)>([和、与]?(.{,3})?<e(\d)>)?[之的]?([^），。；！<>（]{,5})'
    res = re.search(pattern,sent)
    if res:
        a,b= int(res.group(1)),int(res.group(3))
        if a == b:
            return count
        guanxi = res.group(7)
        if guanxi in relation_map:
            guanxi = relation_map[guanxi]
        else:
            guanxi = '其它'
        rela = [entities[a-1],entities[b-1],guanxi]
        print('xi relation:',' '.join(rela))
        if rela not in relations:
            relations.append(rela)
        count+=1
        
        if res.group(6):
            c = int(res.group(6))
            rela = [entities[a-1],entities[c-1],guanxi]
            print('xi relation:',' '.join(rela))
            if rela not in relations:
                relations.append(rela)
            count+=1
    return count
    
def get_shi(sent,entities,relations,relations_map): # a[、与和]b[是系]xx关系
    count = 0
    pattern = '<e(\d)>[和、与]<e(\d)>[是|系]([^），。；！<>]{,3})关系'
    res = re.search(pattern,sent)
    if res:
        a,b = int(res.group(1)),int(res.group(2))
        if a == b:
            return count
        rela = [entities[a-1],entities[b-1],res.group(3)]
        print('shi relation:',' '.join(rela))
        if rela not in relations:
            relations.append(rela)
        count+=1
    return count
    
def get_de(sent,entities,relations,relation_map): # a的xxb
    count = 0
    pattern = '<e(\d)>[的之]([^与，。]{1,2})<e(\d+)>'
    res = re.search(pattern,sent)
    if res:
        a,b = int(res.group(1)),int(res.group(3))
        if a == b:
            return count
        guanxi = res.group(2)
        if guanxi in relation_map:
            guanxi = relation_map[guanxi]
        else:
            guanxi = '其它'
        rela = [entities[b-1],entities[a-1],guanxi]
        print('de relation:',' '.join(rela))
        if rela not in relations:
            relations.append(rela)
        count += 1
    return count

def get_qi(sent,entities,relations,relation_map): # a(其)xxb
    count = 0
    pattern = '<e(\d)>[^<>]*[其]([^中愿间，。！；]{2})<e(\d+)>'
    res = re.search(pattern,sent)
    if res:
        a,b = int(res.group(1)),int(res.group(3))
        if a == b:
            return count
        guanxi = res.group(2)
        if guanxi in relation_map:
            guanxi = relation_map[guanxi]
        else:
            guanxi = '其它'
        rela = [entities[b-1],entities[a-1],guanxi]
        print('qi relation:',' '.join(rela))
        if rela not in relations:
            relations.append(rela)
        count += 1
    return count

def get_children(sent,entities,relations,relation_map):
    count = 0
    pattern = '(原告|被告)?<e(\d)>(.*[我|其])?[与|同|和]?(原告|被告)?<e(\d)>[^。！；<>]*(结婚|婚后|同居)?([^<>]*生[育]?([^活。名]{,4}[，取]?)[名]?<e(\d)>)([^<>]*生[育]?([^活。名]{,4}[，取]?)[名]?<e(\d)>)?([^<>]*生[育]?([^活。名]{,4}[，取]?)[名]?<e(\d)>)?'
    res = re.search(pattern,sent)
    if res:
        a,b = int(res.group(2)),int(res.group(5))
        if a == b:
            return count
        a,b = entities[a-1],entities[b-1]
        for i in range(9,len(res.groups()),3):
            if res.group(i):
                index = int(res.group(i))
                c = entities[index-1]
                gender = res.group(i-1)
                judge_parent(a,c,gender,relations)
                judge_parent(b,c,gender,relations)
                count += 2
    return count

def judge_parent(par,chi,gender,relations):
    rela = None
    if par[0] == chi[0]:
        if '子' in gender or '男' in gender:
            rela = [par,chi,'父子']
        elif '女' in gender:
            rela = [par,chi,'父女']
        elif '孩' in gender:
            rela = [par,chi,'父子女']
    else:
        if '子' in gender or '男' in gender:
            rela = [par,chi,'母子']
        elif '女' in gender:
            rela = [par,chi,'母女']
        elif '孩' in gender:
            rela = [par,chi,'母子女']
    if rela:
        print('children relation:',' '.join(rela))
        if rela not in relations:
                relations.append(rela)


def get_ybgao(sent, target):
    '''提取原被告姓名,有待改进'''
    indexL = sent.index(target)+len(target)
    while sent[indexL] in ['：','）']:
        indexL += 1
    if '，' in sent:
        indexR = sent.index('，')
    else:
        indexR = sent.index('。')
    return sent[indexL:indexR]

def process_daili(relations, ren, gao, guanxi):
    if len(ren) == 0 or len(gao) == 0:
        return;
    if len(ren) > 5 :
        if '（' in ren:
            ren = ren.split('（')[0]
    if len(gao) > 5:
        if '（' in gao:
            gao = gao.split('（')[0]
    if len(gao) > 5:
        return
    
    if '、' in ren:
        for r in ren.split('、'):
            if len(r) <= 5:
                relations.append([r,gao,guanxi])
    else:
        if len(ren) <= 5:
            relations.append([ren,gao,guanxi])

def get_daili_statement(doc):
    try:
        context = doc
        sents = re.split('([。！？；])',context)
        sents = [x+y for x,y in zip(sents[0::2],sents[1::2])]
        daili_relations = []
        for index,sent in enumerate(sents):
            if '原告：' in sent and index+1 < len(sents) and '代理人' in sents[index+1]:
                gao = get_ybgao(sent,'原告：')
                ren = get_ybgao(sents[index+1],'代理人')
                process_daili(daili_relations,ren,gao,'代理人')
            if '原告：' in sent and index+1 < len(sents) and '辩护人' in sents[index+1]:
                gao = get_ybgao(sent,'原告：')
                ren = get_ybgao(sents[index+1],'辩护人')
                process_daili(daili_relations,ren,gao,'辩护人')
            if '被告：' in sent and index+1 < len(sents) and '代理人' in sents[index+1]:
                gao = get_ybgao(sent,'被告：')
                ren = get_ybgao(sents[index+1],'代理人')
                process_daili(daili_relations,ren,gao,'代理人')
            if '被告：' in sent and index+1 < len(sents) and '辩护人' in sents[index+1]:
                gao = get_ybgao(sent,'被告：')
                ren = get_ybgao(sents[index+1],'辩护人')
                process_daili(daili_relations,ren,gao,'辩护人')
            
        return daili_relations
    except Exception as e:
        print(e)

def get_candidate_sentences(doc,thu1,keys):
    '''遍历文书，保存下可能存在关系的句子。每个文书作为一个doc_dict，包括原被告与候选句子'''
        
    try:
        context = doc
        context = re.sub('原、被告','原告和被告 ',context)
        context = re.sub('原被告','原告和被告 ',context)
        sents = re.split('([。！？；])',context)
        sents = [x+y for x,y in zip(sents[0::2],sents[1::2])]
        yuangao = ''
        beigao = ''
        doc_dict = {'原告':'','被告':'','sentences':[]}
        for index,sent in enumerate(sents):
            if (yuangao == '' and '原告' in sent):
                yuangao = get_ybgao(sent,'原告')
                doc_dict['原告'] = yuangao

            if (beigao == '' and '被告' in sent):
                beigao = get_ybgao(sent,'被告')
                doc_dict['被告'] = beigao
            
            tcut = thu1.fast_cut(sent)
            tWords,tFlags = zip(*tcut)
            tWords = list(tWords)
            
            if yuangao != '' and '原告' in tWords:
                for i1 in range(len(tWords)):
                    if i1 > 0 and tFlags[i1-1] == 'm':
                        continue
                    if tWords[i1] == '原告' and tWords[i1+1][0] != yuangao[0]:
                        tWords[i1] = yuangao
                    
            if beigao != '' and  '被告' in tWords:
                for i1 in range(len(tWords)):
                    if i1 > 0 and tFlags[i1-1] == 'm':
                        continue
                    if tWords[i1] == '被告' and tWords[i1+1][0] != beigao[0]:
                        tWords[i1] = beigao
            
            sent = ''.join(tWords)
            pcut = [(x.word,x.flag) for x in pseg.cut(sent)]
            pWords,pFlags = zip(*pcut)
            tcut = thu1.fast_cut(sent)
            tWords,tFlags = zip(*tcut)

            segs1 = [word for word,flag in zip(pWords,pFlags) if flag == 'nr']
            segs2 = [word for word,flag in zip(tWords,tFlags) if flag == 'np']
            segs1 = set(segs1)
            segs2 = set(segs2)
            if (len(segs1) >= 2 or len(segs2) >= 2)and '审判' not in sent and '书记' not in sent and '判决' not in sent:
                for key in keys:
                    if key in sent:
                        doc_dict['sentences'].append(sent)
                        break

    except Exception as e:
        print(e)
            
    return doc_dict


                
def get_entity(sent, entities,thu1):
    '''抽取句子中的人名实体，并替换为<e\d>形式。sent是句子，entities表示本文书中已知的实体。
    先将已知的实体优先替换，之后再抽取新的实体'''
    print(sent)
    for index,entity in enumerate(entities):
        entity = entities[index]
        if entity in sent:
            if len(entity) == 2 and entity[1] == '某':
                tails = ['某','甲','乙','丙','丁','戊']
                for tail in tails:
                    name = entity+tail
                    if name in sent:
                        if name in entities:
                            sent = re.sub(name,'<e'+str(entities.index(name)+1)+'>',sent)
                        else:
                            entities.append(name)
                            sent = re.sub(name,'<e'+str(len(entities))+'>',sent)
            sent = re.sub(entity,'<e'+str(index+1)+'>',sent)
    
    tcut = thu1.fast_cut(sent)
    tWords,tFlags = zip(*tcut)
    tailFlag = ['g','r','m'];
    
    for index,word in enumerate(tWords):
        if tFlags[index] == 'np' and tWords[index][0] != '<':
            if (tFlags[index+1] in tailFlag and len(tWords[index]) < 3) or tWords[index+1] == '×' or (index+2 < len(tWords) 
                                                                         and tWords[index+2] in ['，','、','。'] 
                                                                         and len(tWords[index]) < 3
                                                                         and len(tWords[index]+tWords[index+1])<=3):
                name = tWords[index]+tWords[index+1]
            else:
                name = tWords[index]
            if len(name) < 2:
                continue
            if name not in entities:
                entities.append(name)
            sent = re.sub(name,'<e'+str(entities.index(name)+1)+'>',sent,count=1)
    print(sent)
#     print(entities)
    return sent

def extraction_relations(candidate,thu1,relation_map):
    '''遍历candidates中每个doc_dict，抽取各种相应关系并计数'''
#     print(candidate['uid'])
    entities = []
    if candidate['原告'] != candidate['被告']:
        if len(candidate['原告']) >= 2 and len(candidate['原告']) < 5:
            entities.append(candidate['原告'])
        if len(candidate['被告']) >= 2 and len(candidate['被告']) < 5:
            entities.append(candidate['被告'])
    relations = []
    relationNum = 0
    sentNum = 0
    extractionCount = 0
    for sent in candidate['sentences']:
        sentNum += 1
        sent= get_entity(sent,entities,thu1)
        relationNum += get_couple(sent,entities,relations,relation_map)
        relationNum += get_xi(sent,entities,relations,relation_map)
        relationNum += get_children(sent,entities,relations,relation_map)
        relationNum += get_qi(sent,entities,relations,relation_map)
        relationNum += get_de(sent,entities,relations,relation_map)
        relationNum += get_shi(sent,entities,relations,relation_map)
        relationNum += get_daili(sent,entities,relations,relation_map)
        print()
        if relationNum > 0:
            extractionCount += 1
            relationNum = 0
#     print(entities)
#     print(relations)
#     print('relation extraction time in this essay:',relationNum)
#     print('relation number in this essay:',len(relations))
#     print('entity number in this essay:',len(entities))
#     print()
    return entities, relations

class PersonRelationExtractor(object):
    def __init__(self):
        data = {
                "丈夫": ["丈夫","夫"],
                "妻子": ["妻子","妻"],
                "前妻": ["前妻"],
                "前夫": ["前夫"],
                "父亲": ["父","父亲"],
                "母亲": ["母","母亲"],
                "儿子": ["子","独生子","一子","二子","三子","四子","五子","儿子","次子","婚生子","长子","男孩","非婚生子","婚生儿子","非婚生儿子"],
                "女儿": ["女","独生女","一女","二女","三女","四女","五女","女儿","次女","婚生女","长女","女孩","非婚生女","婚生女儿","非婚生女儿"],
                "兄弟": ["胞兄","大哥","哥","兄","弟","弟弟","胞弟","表哥","哥哥","表弟","兄长"],
                "姐妹": ["姐姐","妹妹","大姐","二姐","三姐","姐","妹"],
                "叔伯": ["叔叔","表叔","大伯","叔父","伯父","堂叔"],
                "姑婶": ["婶婶","婶子","婶娘","姑妈","姑姑","大姑","大姑妈","二姑","二姑妈"],
                "侄子女": ["侄子","侄女","侄儿","侄"],
                "舅舅": ["舅","大舅","二舅","舅舅"],
                "舅妈": ["舅妈"],
                "姨": ["大姨","二姨","姨妈","三姨","四姨","小姨"],
                "外甥": ["外甥","外甥女"],
                "配偶父母": ["婆婆","公公","岳父","岳母"],
                "爷爷": ["爷爷","祖父"],
                "奶奶": ["奶奶","祖母"],
                "姥姥": ["姥姥","外祖母","外婆"],
                "姥爷": ["姥爷","外祖父","外公"],
                "孙子女": ["孙","孙子","孙女","外孙","外孙女"],
                "同学朋友":["朋友","同学","好友"]
                }
        tmp = [[y,x] for x in data for y in data[x]]
        self.relation_map = dict(tmp)
        self.keys = ['兄','弟','姐','妹','哥','父','母','叔','侄','奶','爷','孙子','姑','舅','甥','姨',
        '妈','爸','友','夫','妻','邻','徒','媳','伯','婿','婚']
        self.cutter = thulac.thulac(user_dict='../data/word_dict.txt')
        
    def work(self, context):
        try:
            daili_relations = get_daili_statement(context)
            candidate = get_candidate_sentences(context,self.cutter,self.keys)
            entities, relations = extraction_relations(candidate,self.cutter,self.relation_map)
            relations += daili_relations
            print(entities)
            print(relations)
            return entities,relations
        except Exception as e:
            print(e)
        

def main():
    import pandas as pd
    try:
        pre = PersonRelationExtractor()
        f = open('../data/sample.json')
        doc_lists = json.load(f)
        df = pd.DataFrame(doc_lists)
        while True:
            uid = input('请输入文书uid（或输入q退出）：')
            if uid == 'q':
                break;
            qw = df[df['uid'] == uid].iloc[0]
            print(qw.QW)
            entities, relations = pre.work(qw.QW)
            print('extracted entities:',entities)
            print('extracted relations:',relations)
    except Exception as e:
        print(e)
        return 2
    
    
if __name__ == '__main__':
    main()
#     filepath = '../data/gg.json'
#     f = open(filepath)
#     lines = f.readlines()
#     datas = [json.loads(line) for line in lines]
    
#     pre = PersonRelationExtractor()
#     for i in range(10000):
#         d = datas[i]
#         print(d['uid'])
#         pre.work(d['QW'])
    
#     f.close()

Model loaded succeed
90c06132-2cca-4fce-99b3-247faf47e456


Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.868 seconds.
Prefix dict has been built succesfully.


证明金某的母亲与敖德力格尔（德力格尔）离婚时，敖德力格尔（德力格尔）每月承担200元的抚养费。
证明<e1>的母亲与<e2>（<e3>）离婚时，<e2>（<e3>）每月承担200元的抚养费。

本院认证为，该证据能够证明金某的父母离婚时，敖德力格尔（德力格尔）每月承担抚养费200元，为有效证据，予以采信。
本院认证为，该证据能够证明<e1>的父母离婚时，<e2>（<e3>）每月承担抚养费200元，为有效证据，予以采信。

['金某', '敖德力格尔', '德力格尔']
[]
592e4b81-39d4-4c0f-9e37-c329db1100d8
另查明，刘某乙、刘某甲与刘爱英（2008年1月14日死亡）分别系兄妹、姐妹关系。
另查明，<e1>、<e2>与<e3>（2008年1月14日死亡）分别系兄妹、姐妹关系。

刘爱英另有姐妹刘明秀（1998年因死亡注销户口）、刘美丽（1959年死亡），刘爱英的母亲詹三弟于1977年因死亡注销户口，刘爱英的父亲早于詹三弟死亡。
<e3>另有姐妹<e4>（1998年因死亡注销户口）、<e5>（1959年死亡），<e3>的母亲詹三弟于1977年因死亡注销户口，<e3>的父亲早于詹三弟死亡。

刘爱英与丈夫程玉歧（1997年死亡）曾收养一子程海峰，于1981年3月经桂林市秀峰区人民法院调解解除养父母与养子关系，刘爱英无其他子女。
<e3>与丈夫<e6>（1997年死亡）曾收养一子<e7>，于1981年3月经桂林市秀峰区人民法院调解解除养父母与养子关系，<e3>无其他子女。

['刘某乙', '刘某甲', '刘爱英', '刘明秀', '刘美丽', '程玉歧', '程海峰']
[]
cd2fd676-ad5e-4491-bf6f-5decb82cd1e2
原告刘某甲起诉称：刘某甲和刘某乙的妹妹刘爱英生前存入杭州市羊坝头工商银行定期存单10000元。
原告<e1>起诉称：<e1>和<e2>的妹妹<e3>生前存入杭州市羊坝头工商银行定期存单10000元。
de relation: 刘爱英 刘某乙 姐妹

刘爱英夫妇家境富有，没有子女，其与配偶名下房产都已被刘某甲占有，其房子、金器、存折都被刘某甲卖掉，足够清偿其债务。
<e3>夫妇家境富有，没有子女，其与配偶名下房产都已被<e1>占有，其房子、金器、存折都被<e1>卖掉，足够清偿其债务。

另

杨某郝某某（杨某之妻），女，1957年10月20日出生，汉族，农民。
<e1>郝某某（<e1>之妻），女，1957年10月20日出生，汉族，农民。

但杨某某一直未对杨某尽赡养义务，且杨某某之妻辱骂、殴打杨某，向杨某索要土地补偿款。
但<e2>一直未对<e1>尽赡养义务，且<e2>之妻辱骂、殴打<e1>，向<e1>索要土地补偿款。

被告杨某某辩称，大约7、8年前，杨广运（杨某之长兄）、杨广东（杨某之二兄、杨某某之父）、杨某曾商量过由杨某某扶养杨某之事。
被告<e2>辩称，大约7、8年前，<e3>（<e1>之长兄）、<e4>（<e1>之二兄、<e2>之父）、<e1>曾商量过由<e2>扶养<e1>之事。

杨某某之妻给杨某拆洗过一次被子。
<e2>之妻给<e1>拆洗过一次被子。
de relation: 杨某 杨某某 其它

不久，杨广东及杨某某之妻向杨某索要土地补偿款，因杨某未给，即经常殴打、骚扰杨某。
不久，<e4>及<e2>之妻向<e1>索要土地补偿款，因<e1>未给，即经常殴打、骚扰<e1>。
de relation: 杨某 杨某某 其它

根据合议庭对证据效力的认定意见，结合杨某陈述和杨某某答辩，查明本案法律事实如下：杨广运、杨广东、杨某系同胞兄弟。
根据合议庭对证据效力的认定意见，结合<e1>陈述和<e2>答辩，查明本案法律事实如下：<e3>、<e4>、<e1>系同胞兄弟。

杨某、郝某某（系残疾人）夫妇未曾生育子女。
<e1>、郝某某（系残疾人）夫妇未曾生育子女。

2009年前后，杨某当面要求杨某某扶养其夫妇、其夫妇死后的财产给杨某某；
2009年前后，<e1>当面要求<e2>扶养其夫妇、其夫妇死后的财产给<e2>；

杨某某及其妻曾给杨某夫妇做家务活，如给其耕做家庭承包地数年、杨某某之妻给杨某夫妇拆洗被子。
<e2>及其妻曾给<e1>夫妇做家务活，如给其耕做家庭承包地数年、<e2>之妻给<e1>夫妇拆洗被子。
de relation: 杨某 杨某某 其它

2012年春节期间，杨某某之妻给杨某现金200元；
2012年春节期间，<e2>之妻给<e1>现金200元；
de relation: 杨某 杨某某 其它

本院认为，原告杨某于2009年前后向杨某某当面提出，由杨某某扶养其夫妇、其夫妇死后的财产给杨某某，杨某某表示同意，其合意内容符合遗赠扶养协议

原审法院经审理查明，陈某甲的法定代理人庄某与陈某乙于××××年××月××日登记结婚，于2007年11月24日生育陈某甲，于2009年9月30日登记离婚。
原审法院经审理查明，<e1>的法定代理人<e3>与<e2>于××××年××月××日登记结婚，于2007年11月24日生育<e1>，于2009年9月30日登记离婚。
couple relation: 庄某 陈某乙 夫妻

庄某与陈某乙曾于2009年9月30日签订离婚协议书，约定陈某甲由庄某直接抚养，所有费用由庄某承担，陈某乙无需支付。
<e3>与<e2>曾于2009年9月30日签订离婚协议书，约定<e1>由<e3>直接抚养，所有费用由<e3>承担，<e2>无需支付。
couple relation: 庄某 陈某乙 夫妻

陈某甲主张庄某与陈某乙在办理离婚手续后实际仍继续共同居住，直至2011年12月才正式分居，分居时双方口头协议陈某乙每月支付2000元左右的抚养费给陈某甲，因此在2012年9月以前陈某乙曾经陆续按每月2000元的标准支付过抚养费。
<e1>主张<e3>与<e2>在办理离婚手续后实际仍继续共同居住，直至2011年12月才正式分居，分居时双方口头协议<e2>每月支付2000元左右的抚养费给<e1>，因此在2012年9月以前<e2>曾经陆续按每月2000元的标准支付过抚养费。
couple relation: 庄某 陈某乙 夫妻

原审法院认定上述事实的证据有：陈某甲提交的结婚证、离婚证、离婚协议书、出生医学证明、银行卡流水记录、个人收入证明，陈某乙提交的银行卡流水记录以及本案原审庭审笔录等。
原审法院认定上述事实的证据有：<e1>提交的结婚证、离婚证、离婚协议书、出生医学证明、银行卡流水记录、个人收入证明，<e2>提交的银行卡流水记录以及本案原审庭审笔录等。

双方均确认陈某乙从2012年9月开始就没有再支付抚养费，但庄某、陈某乙在离婚时曾经协议陈某乙无需支付抚养费，且没有证据显示从2012年9月以来陈某甲有重大的费用支出，因此原审法院对陈某甲要求陈某乙支付2012年9月至陈某甲提起本案诉讼（2015年3月）期间的抚养费的诉讼请求不予支持。
双方均确认<e2>从2012年9月开始就没有再支付抚养费，但<e3>、<e2>在离婚时曾经协议<e2>无需支付抚养费，且没有证据显示从2012年9月以来<e1>有重大

...

法定代理人肖某丙，男，住株洲县，系原告肖某甲之父。
法定代理人<e3>，男，住株洲县，系原告<e1>之父。

原告肖某甲诉称，肖某甲与被告系母女关系。
原告<e1>诉称，<e1>与被告系母女关系。

肖某甲之父与刘某离婚后，肖某甲与父亲共同生活。
<e1>之父与<e2>离婚后，<e1>与父亲共同生活。

本院对肖某甲提供的证据予以确认，并确认本案案件事实如下：原告肖某甲之父肖某丙与被告刘某曾系夫妻关系，双方于2011年3月1日共同生育原告肖某甲。
本院对<e1>提供的证据予以确认，并确认本案案件事实如下：原告<e1>之父<e3>与被告<e2>曾系夫妻关系，双方于2011年3月1日共同生育原告<e1>。
couple relation: 肖某丙 刘某 夫妻
de relation: 肖某丙 肖某甲 父亲

2014年7月25日，肖某甲之父肖某丙与被告刘某在株洲县民政局协议离婚，双方约定“原告肖某甲归肖某丙抚养，刘某只有探望权”。
2014年7月25日，<e1>之父<e3>与被告<e2>在株洲县民政局协议离婚，双方约定“原告<e1>归<e3>抚养，<e2>只有探望权”。
couple relation: 肖某丙 刘某 夫妻
de relation: 肖某丙 肖某甲 父亲

因肖某丙与被告刘某协议离婚时对原告肖某甲抚养费之事未进行约定，肖某甲诉来本院，要求上述诉讼请求。
因<e3>与被告<e2>协议离婚时对原告<e1>抚养费之事未进行约定，<e1>诉来本院，要求上述诉讼请求。
couple relation: 肖某丙 刘某 夫妻

['肖某甲', '刘某', '肖某丙']
[['肖某丙', '刘某', '夫妻'], ['肖某丙', '肖某甲', '父亲']]
b31b4f10-df25-425d-9faa-5f40aaf962b8
原告赵某某诉称，赵某某和廖某某双方于2009年经人介绍未办理婚姻登记而同居，2010年8月生育长子廖某甲，2012年生育次女廖某乙。
原告<e1>诉称，<e1>和<e2>双方于2009年经人介绍未办理婚姻登记而同居，2010年8月生育长子<e3>，2012年生育次女<e4>。
couple relation: 赵某某 廖某某 夫妻
children relation: 赵某某 廖某甲 母子
children relation: 廖某某 廖某甲 

本院收到<e1>、<e2>的起诉状，诉称：2005年9月23日，<e1>与前妻<e3>协议离婚，约定婚生子<e4>由于世久抚养。

离婚后不久，于克寅实际一直随范梅生活。
离婚后不久，<e4>实际一直随<e3>生活。

2006年12月，于世久与前妻范梅签订抚养协议，将孩子变更为范梅抚养，并办理公证。
2006年12月，<e1>与前妻<e3>签订抚养协议，将孩子变更为<e3>抚养，并办理公证。

['于世久', '薛纪莲', '范梅', '于克寅']
[]
6947b93d-0b73-4190-bd84-22f4deb6101b
原告邓某某诉称，邓某某婚后共生育六个子女，邓某某自丈夫去世后，体弱多病，生活困难，邓某某遂要求六被告履行赡养义务，但被告林A、林D未支付赡养费，邓某某生病也未进行护理。
原告<e1>诉称，<e1>婚后共生育六个子女，<e1>自丈夫去世后，体弱多病，生活困难，<e1>遂要求六被告履行赡养义务，但被告<e2>、林D未支付赡养费，<e1>生病也未进行护理。

经审理查明，邓某某与丈夫婚后共生育六个子女，即：本案六被告，邓某某及丈夫将六被告抚养成年，现邓某某年老无生活来源。
经审理查明，<e1>与丈夫婚后共生育六个子女，即：本案六被告，<e1>及丈夫将六被告抚养成年，现<e1>年老无生活来源。

['邓某某', '林A']
[]
23f0d0aa-1035-4e3b-82c7-bef2be8c98cd
['屈某', '刘某']
[]
e59d3df2-617e-4b3b-8181-ae075b040486
本院在审理原告周海波诉被告王秋敏、王银堂婚约财产纠纷一案中，原告周海波于2015年8月3日向本院申请撤回起诉。
本院在审理原告<e1>诉被告<e2>、<e3>婚约财产纠纷一案中，原告<e1>于2015年8月3日向本院申请撤回起诉。

['周海波', '王秋敏', '王银堂']
[]
5f4d76cc-291c-4f26-b5d5-136326211aa4
经审理查明，刘某某系吴某某之母，被告系吴某某之父。
经审理查明，<e3>系<e1>之母，被告系<e1>之父。
xi relation: 刘某某 吴某某 母亲

2014年1月10日，刘某某与吴某甲在广饶县民政局协议离婚，双方在离婚协议中约定吴某某由刘某某抚养，吴某甲每月支付其抚养费1000元直至

原审原告田某原审诉称，1953年我的母亲李淑芳在本村有房屋一栋，1968年我的父亲田寿山去世，父亲去世时我的爷爷奶奶均早已去世。
原审原告<e1>原审诉称，1953年我的母亲<e3>在本村有房屋一栋，1968年我的父亲<e4>去世，父亲去世时我的爷爷奶奶均早已去世。

××××年李淑芳与于秀云登记结婚，婚后双方在于秀云处居住，1979年李淑芳又搬回本村居住至去世。
××××年<e3>与<e5>登记结婚，婚后双方在于秀云处居住，1979年<e3>又搬回本村居住至去世。
couple relation: 李淑芳 于秀云 夫妻

因于秀云与李淑芳系夫妻关系，须由其到房管部门协助方可办理房产过户手续，但于秀云不予配合，故诉至法院，要求确认上述房屋归田某所有。
因<e5>与<e3>系夫妻关系，须由其到房管部门协助方可办理房产过户手续，但<e5>不予配合，故诉至法院，要求确认上述房屋归<e1>所有。
couple relation: 于秀云 李淑芳 夫妻
shi relation: 于秀云 李淑芳 夫妻

五原审被告于某甲、于某乙、于某丙、于某丁、于某戊共同辩称，田某所诉争的房屋系于秀云与李淑芳的婚后共同财产，该房屋作为于秀云与李淑芳的遗产，不应归田某所有，由田某和于某甲依法继承。
五原审被告<e2>、于某乙、于某丙、<e6>、于某戊共同辩称，<e1>所诉争的房屋系<e5>与<e3>的婚后共同财产，该房屋作为<e5>与<e3>的遗产，不应归<e1>所有，由<e1>和<e2>依法继承。
couple relation: 于秀云 李淑芳 夫妻

原审法院审理查明，田某的父亲田寿山与母亲李淑芳婚后只生育田某。
原审法院审理查明，<e1>的父亲<e4>与母亲<e3>婚后只生育<e1>。
de relation: 田寿山 田某 父亲

李淑芳与于秀云于××××年结婚，李淑芳于2014年2月4日去世，李淑芳的父母亦早于其去世。
<e3>与<e5>于××××年结婚，<e3>于2014年2月4日去世，<e3>的父母亦早于其去世。
couple relation: 李淑芳 于秀云 夫妻

李淑芳与于秀云婚后未生育子女，二人结婚时，于秀云与前妻生育四名子女，长子于春龙、次子于某丙、长女于某甲、次女于某乙。
<e3>与<e5>婚后未生育子女，二人结婚时，<e5>与前妻生育四名子女，长子<e7>、次子

被继承人<e3>去世时，其第一顺位的继承人有本案的<e1>（<e3>之母）及被告<e2>（<e3>之妻）、于某某（<e3>之子）。

['宫某某', '王某某', '于甲']
[['于甲', '王某某', '夫妻'], ['宫某某', '于甲', '母亲']]
875163f3-0103-4f45-96cc-ee56c8e2f3ad
及两原告代理人的母亲周瑞堂、周瑞丛、周瑞敏、周瑞坤辩称：刘玉珍的代理人周文侠、周瑞峰并未征得原告刘玉珍的授权委托，诉状中的请求事项不是母亲的真实意思表示，是周文侠、周瑞峰假借刘玉珍之名提起的虚假诉讼。
及两原告代理人的母亲<e2>、<e3>、<e4>、<e5>辩称：<e1>的代理人<e6>、<e7>并未征得原告<e1>的授权委托，诉状中的请求事项不是母亲的真实意思表示，是<e6>、<e7>假借<e1>之名提起的虚假诉讼。

四被告一直与母亲刘玉珍生活在凌源市小城子镇修杖子村五组，一直由四被告照顾。
四被告一直与母亲<e1>生活在凌源市小城子镇修杖子村五组，一直由四被告照顾。

刘玉珍代理人周瑞峰无理取闹，阻碍及两原告代理人的母亲几家探望护理刘玉珍。
<e1>代理人<e7>无理取闹，阻碍及两原告代理人的母亲几家探望护理<e1>。

经审理查明，原告刘玉珍与其丈夫周作银生育六名子女，分别是长子周瑞堂、次子周瑞丛、三子周瑞敏、四子周瑞坤、五子周瑞峰及长女周文侠。
经审理查明，原告<e1>与其丈夫<e8>生育六名子女，分别是长子<e2>、次子<e3>、三子<e4>、四子<e5>、五子<e7>及长女<e6>。
qi relation: 周作银 刘玉珍 丈夫

及两原告代理人的母亲周瑞堂、周瑞丛、周瑞敏、周瑞坤每人拿出5，000元作为刘玉珍的医疗费，后刘玉珍病情加重被转入ICU重症监护病房治疗。
及两原告代理人的母亲<e2>、<e3>、<e4>、<e5>每人拿出5，000元作为<e1>的医疗费，后<e1>病情加重被转入ICU重症监护病房治疗。

上述事实，有刘玉珍和及两原告代理人的母亲陈述，住院诊断及报销收据等证据在卷佐证，并经庭审质证和本院审查，可以采信。
上述事实，有<e1>和及两原告代理人的母亲陈述，住院诊断及报销收据等证据在卷佐证，并经庭审质证和本院审查，可以采信。

案件受理费减半收取50元，由及两原告代理人的母亲周瑞堂、周瑞丛、周瑞敏、

理由如下：1．被申请人陈某乙有2.6亩的承包田及大儿媳母子的承包田，申请再审人夫妻及母亲陈某某三口人的承包田都由被申请人耕种，承包田合计16.08亩，按每亩纯收入500元计算，不包括粮食直补款，纯收入8000余元，超过了辽宁省农村居民人均年生活费支出的最低规定，申请再审人无需再给付赡养费。
理由如下：1．被申请人<e1>有2.6亩的承包田及大儿媳母子的承包田，申请再审人夫妻及母亲<e2>三口人的承包田都由被申请人耕种，承包田合计16.08亩，按每亩纯收入500元计算，不包括粮食直补款，纯收入8000余元，超过了辽宁省农村居民人均年生活费支出的最低规定，申请再审人无需再给付赡养费。

被申请人陈某乙答辩称，申请再审人陈某甲称我有2.6亩承包田，事实是此地系大儿媳母子的承包田，我是代为管理，收入完全归大儿媳所有，至于承包田根本就是子虚乌有。
被申请人<e1>答辩称，申请再审人<e3>甲称我有2.6亩承包田，事实是此地系大儿媳母子的承包田，我是代为管理，收入完全归大儿媳所有，至于承包田根本就是子虚乌有。

['陈某乙', '陈某某', '陈某']
[]
afcf04da-60f7-4955-994a-80679f77b9b6
另查明，陈某某的2.67亩承包田及大儿媳母子的承包田现由陈某某耕种。
另查明，<e1>的2.67亩承包田及大儿媳母子的承包田现由<e1>耕种。

1、被上诉人有2.67亩承包田及大儿媳母子的承包田，上诉人夫妻及母亲三口人的承包田也由被上诉人耕种，承包田合计16.08亩，按每亩纯收入500元计算，不包括粮食直补纯收入8000余元，超过了辽宁省农村居民人均年生活费支出，上诉人无需给付赡养费；
1、被上诉人有2.67亩承包田及大儿媳母子的承包田，上诉人夫妻及母亲三口人的承包田也由被上诉人耕种，承包田合计16.08亩，按每亩纯收入500元计算，不包括粮食直补纯收入8000余元，超过了辽宁省农村居民人均年生活费支出，上诉人无需给付赡养费；

['陈某某']
[]
cee394a1-333d-4859-8f4b-3711a3fa79ad
['张利强', '武俊红']
[]
af8faba4-a4ba-4205-92ad-b52a9d5b0896
经审理查明，原告王某崇1997年11月2日出生，系提高生活标准2006年-2015年50400元王某伟与前妻李某红婚生

In [4]:
import re
sent = '另：庭审中<e1>陈述婚生男孩<e3>一直跟随其奶奶<e4>生活。'

pattern = '<e(\d)>[^<>]*[其]([^中愿间，。！；]{2})<e(\d+)>'
res = re.search(pattern,sent)
if res:
    print(res.groups())

('3', '奶奶', '4')


In [24]:


f = open('../data/non_gg1.json')
lines = f.readlines()

for i in range(1000):
    d = json.loads(lines[i])
    print(d['uid'])
    print(get_daili_statement(d['QW']))

f.close()

90c06132-2cca-4fce-99b3-247faf47e456
[]
592e4b81-39d4-4c0f-9e37-c329db1100d8
[]
cd2fd676-ad5e-4491-bf6f-5decb82cd1e2
[['汪荣行', '刘某乙', '代理人']]
584b7598-e999-4818-b2b1-00b9035a0ed7
[['蒋江', '赵新燕', '代理人'], ['刘振江', '赵新光', '代理人'], ['方建利', '赵振海', '代理人']]
a8fa6473-cfcc-42d2-b694-8177a11b224a
[]
8df54f4d-a77a-435c-b828-a1cf7d9a4edb
[['胡德云', '王某', '代理人'], ['洪华芬', '董某', '代理人']]
3672e98b-6d99-42a1-9453-9f78149d115e
[['黄志明', '李某', '代理人']]
db112dc5-9e87-405f-b2e3-8ffc9e3472f3
[]
d12fec53-e0ba-4b03-b93c-3425dce40271
[['赵受政', '蔡某', '代理人']]
041b2a83-d5cc-4955-892c-38d7a2c262a7
[]
0f962dc4-ff05-4d3f-b1ea-ad142e38fcda
[]
97565e9f-9932-4f19-be75-0e14b7d68c92
[]
386b6d62-fcc8-44dd-a623-f1bd7814840a
[]
2991ef39-14aa-469b-b76e-e2907eaba7f4
[]
6cfaa206-b863-4029-a739-eb20109e3c5f
[]
1c58b9cb-3192-450f-80d3-5354785b14bb
[]
de46e94e-0176-4d6c-b09c-5bdb43cef24c
[]
4ffffc8a-5afb-4f6a-9430-1fe96f3c98d3
[]
357ad1fd-9eac-4001-951a-d4a35d363b38
[]
b09625b7-1032-4f90-9a34-9fce59e801f7
[]
c53df42d-5cb9-47dc-ac64-fcb584e

01f8403a-c058-4703-9c1d-e27868aea2c3
[]
5c2b06bd-6b64-4731-901c-91a63f6893b4
[]
cf48588c-0f39-40fd-8c71-a4b9b38b08e9
[]
3d3ed5b0-5530-4a52-ab70-a68d5b2b3255
[['时学宣', '杜某', '代理人']]
d81e42d0-2a20-4f1f-b2a0-f1fefebe56f3
[]
2fd4b4bc-7016-4442-b599-f3bdb49628d4
[]
bd3146d8-a728-430b-afaf-99346095db67
[['费龙洋', '郑某1', '代理人'], ['李健伟', '郑某4', '代理人']]
4af88aae-be3f-4db4-8ce9-0acd72ef6a11
[]
9418ed94-d928-43b3-a0de-13a39c30926e
[]
a2a3e447-5106-4644-89c0-96c1ad4d127a
[['刘绪兰', '刘家富', '代理人'], ['徐巧月', '王玲', '代理人']]
03ee9fe9-efef-4a78-8147-10d9b18bf20e
[]
c7de9b36-bc98-47ff-9a00-0f78f6a7aaef
[]
84f1c90d-f480-4e62-ab6b-dc9caf8cd4cd
[]
1da2819e-2a27-42c8-8f24-aad62d1ce945
[]
0e2ced2b-65d1-48ec-aff2-7dab446e2a43
[]
7888e8b6-87dc-47ba-aa27-b86d0d79a90b
[['李兴涛', '罗树珍', '代理人']]
4e2fe749-4736-41a0-bf51-29b05c4b55b5
[]
c0071465-964b-4106-9a45-5fede622d28d
[]
dd118c46-f0fd-4a45-8900-1f1337288636
[]
e913dca1-456e-4aac-8e8b-87a282f167b8
[['李越明', '顾长生', '代理人'], ['徐海明', '李聪', '代理人']]
df54f33c-118e-4cd9-b046-db100

7a8b7e69-de31-4a43-86eb-ad3a6820788f
[['邱宝卫', '颜某甲', '代理人'], ['虞一专', '颜某甲', '代理人']]
43637a45-a382-41f7-b15d-a1796e93ba24
[['陈某甲', '王某乙', '代理人'], ['王某戊', '王某丙', '代理人']]
83a8799f-0d8d-435b-b257-f4f068d3f1f0
[['智德学', '赵某', '代理人']]
acfb9da5-60ee-4d2d-ace1-d6c82270d081
[['魏德群', '林某某', '代理人']]
43824e2c-8da5-4466-aeb0-d6f248097ff7
[]
b9b65ea8-fdcc-42ad-a2a5-7e51184c982e
[]
44b67400-91f9-4fe0-a388-3e240e4682f1
[]
dc342df5-dab9-4c99-ad4b-304b46b05540
[]
7de42584-94f7-4bff-8eef-2726a683850a
[]
9efa7704-ccea-4b7f-9a87-5ff7569fa034
[['杨浩', '王某', '代理人']]
00470795-920e-49a2-bae1-70ab2b7fd951
[]
1a6ec137-06ed-41ce-90fc-1b7034949339
[]
2bbff4e6-d4cd-45f0-bea3-05853ea9198d
[['陈某3', '陈某2', '代理人']]
4ecdec1b-e675-4215-9fd9-8b678c82d96f
[['侯宝波', '杨某', '代理人']]
4f339d66-655a-438c-8573-db2178ac3efb
[['向晓燕', '刘某芝', '代理人']]
7f4d474b-ae82-48d1-87c1-b9080416c190
[]
6144be84-3a90-4d96-8eea-22f89f958b68
[]
fa9c5cfa-0aaf-4fb3-8099-97afd4bbc176
[['侯佰锋', '王某', '代理人']]
2004cea9-bbb6-4db8-95b8-f95bba0eff50
[['高旭东', '张某'

[]
3adf0902-5d42-4462-8f6a-24e243c9c105
[]
a1332801-9d3d-41d3-8293-f7443e2d2b77
[]
f34c16aa-6453-429e-8453-b3f98e4d87b8
[]
1d597078-c486-4344-bbc4-1d11c253a0f4
[]
bd063ceb-bd53-4310-9b83-0830c409581e
[]
e31df1c5-0403-44b2-9295-da6fcb172c45
[]
bb1fed3b-9fba-4068-ba52-10ca98ef5b4d
[]
b76fa756-fef4-48cb-be14-55dd0ee05dd8
[]
bc0a766f-7375-48d6-b704-21d0e1395397
[]
1feb1037-e75a-4645-b53b-b6d1af8e6385
[]
30413178-a5e9-4864-9678-0d993941a1a7
[]
5062d826-15f0-4023-af00-b1a2d7cfe597
[]
8d8339e3-cefe-4b22-9246-9be15744e868
[]
6e1e43e4-fad6-449c-acd9-1b3892792254
[]
7b84b7ca-ccbc-404c-98fd-da827ce0c031
[]
c898bc94-b818-413b-b01e-0b061e30738a
[['张清水', '张某某', '代理人']]
50f9f62c-b1b8-4bcb-b9a9-cebecf477079
[['杨霞', '查某芳', '代理人'], ['文晓敏', '查某政', '代理人']]
ece0dbbe-7794-4755-9bcb-1edf7ddca805
[]
02f0559c-7303-422c-92ef-37b41c33a994
[]
c314ee9a-92d7-4a85-9087-0197cf39e5f8
[]
27b490ff-5a34-4240-ab53-1466a0a7e95b
[]
d8f2cb8c-2f7a-48ff-825d-612dd971c23e
[['董某', '赵某', '代理人'], ['谌东', '周某', '代理人']]
471ca04b-4cca

In [32]:
sent = '经审理查明，经人介绍相识后，原告马×与被告杜×某于2013年农历2月12日订立婚约，订婚时，马×方向被告方押彩礼现金26000元。'
cuts = [x for x in pseg.cut(sent)]
print(cuts)

[pair('经', 'n'), pair('审理', 'vn'), pair('查明', 'nr'), pair('，', 'x'), pair('经人介绍', 'nr'), pair('相识', 'v'), pair('后', 'f'), pair('，', 'x'), pair('原告', 'n'), pair('马', 'n'), pair('×', 'x'), pair('与', 'p'), pair('被告', 'n'), pair('杜', 'nr'), pair('×', 'x'), pair('某', 'r'), pair('于', 'p'), pair('2013', 'm'), pair('年', 'm'), pair('农历', 'n'), pair('2', 'm'), pair('月', 'm'), pair('12', 'm'), pair('日', 'm'), pair('订立', 'v'), pair('婚约', 'n'), pair('，', 'x'), pair('订婚', 'v'), pair('时', 'n'), pair('，', 'x'), pair('马', 'n'), pair('×', 'x'), pair('方向', 'n'), pair('被告方', 'n'), pair('押', 'zg'), pair('彩礼', 'n'), pair('现金', 'n'), pair('26000', 'm'), pair('元', 'm'), pair('。', 'x')]


In [2]:
import json

f = open('../data/gg.json')
fin = open('../data/non_gg10w.json','w')
i = 0
while i < 100000:
    line = f.readline()
    d = json.loads(line)
    if '离婚' not in d['TITLE']:
        s = json.dumps(d)
        fin.write(s+'\n')
        i += 1
        if i%100 == 0:
            print(i)
fin.close()
f.close()

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200
11300
11400
11500
11600
11700
11800
11900
12000
12100
12200
12300
12400
12500
12600
12700
12800
12900
13000
13100
13200
13300
13400
13500
13600
13700
13800
13900
14000
14100
14200
14300
14400
14500
14600
14700
14800
14900
15000
15100
15200
15300
15400
15500
15600
15700
15800
15900
16000
16100
16200
16300
16400
16500
16600
16700
16800
16900
17000
17100
17200
17300
17400
17500
17600
17700
17800
17900
18000
18100
18200
18300
18400
1850